<a href="https://colab.research.google.com/github/timovijn/ElectricityPriceForecasting/blob/master/LSTM/LSTM%20confidence.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Bayesian LSTM for electricity price prediction**

**Monte Carlo dropout as an approximation for Bayesian Inference**

Timo Vijn

# Required packages

In [1]:
import pandas as pd
import numpy as np

hex_salmon = '#F68F83'
hex_gold = '#BC9661'
hex_indigo = '#2D2E5F'
hex_maroon = '#8C4750'
hex_white = '#FAFAFA'
hex_blue = '#7EB5D2'

import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib as mpl
from matplotlib.dates import DateFormatter
import matplotlib.dates as dates

import matplotlib.font_manager as font_manager
mpl.font_manager._rebuild()

mpl.rcParams['font.family'] = 'SF Mono'
mpl.rcParams['font.weight'] = 'medium'
mpl.rcParams['axes.titleweight'] = 'semibold'
mpl.rcParams['axes.labelweight'] = 'medium'
mpl.rcParams['axes.prop_cycle'] = mpl.cycler(color=[hex_indigo, hex_salmon, hex_maroon])
mpl.rcParams["figure.titlesize"] = 'large'
mpl.rcParams["figure.titleweight"] = 'semibold'

from termcolor import colored

from sklearn.model_selection import train_test_split
from sklearn.linear_model import Lasso, LogisticRegression, Ridge, ElasticNet, LassoCV, RidgeCV, ElasticNetCV
from sklearn.feature_selection import SelectFromModel
from sklearn.preprocessing import StandardScaler, MinMaxScaler, LabelEncoder
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.metrics import roc_auc_score, accuracy_score

import tensorflow as tf

# Load data

## Clone from Github

In [2]:
! pip install 'git+git://github.com/HR/github-clone#egg=ghclone' &> /dev/null

! ghclone https://github.com/timovijn/ElectricityPriceForecasting/tree/master/LSTM

Cloning into 'LSTM'...
done.


## Load features dataframe

In [3]:
features = pd.read_pickle(f"./LSTM/features2.pkl")

print(colored(f'Load complete', 'green'))

Load complete


In [4]:
features.head(5)

ID3   VOL    MCP  ...  HOD 21  HOD 22  HOD 23
2015-01-01 05:00:00+00:00  27.500000  29.0  27.41  ...       0       0       0
2015-01-01 06:00:00+00:00  26.780822  28.0  27.52  ...       0       0       0
2015-01-01 07:00:00+00:00  25.852273  65.0  26.80  ...       0       0       0
2015-01-01 08:00:00+00:00  24.400000  18.0  28.48  ...       0       0       0
2015-01-01 09:00:00+00:00  25.625000  15.0  27.71  ...       0       0       0

[5 rows x 239 columns]

## Extract features

In [5]:
features = features[['DOW', 'HOD', 'ID3']]

features = features.reset_index()

features = features.rename(columns={'index':'Date'})

In [6]:
features.head(5)

Date  DOW  HOD        ID3
0 2015-01-01 05:00:00+00:00    3    5  27.500000
1 2015-01-01 06:00:00+00:00    3    6  26.780822
2 2015-01-01 07:00:00+00:00    3    7  25.852273
3 2015-01-01 08:00:00+00:00    3    8  24.400000
4 2015-01-01 09:00:00+00:00    3    9  25.625000

In [7]:
features.tail(5)

Date  DOW  HOD        ID3
33840 2018-12-21 23:00:00+00:00    4   23  50.911996
33841 2018-12-22 00:00:00+00:00    5    0  53.554378
33842 2018-12-22 01:00:00+00:00    5    1  53.716854
33843 2018-12-22 02:00:00+00:00    5    2  52.950763
33844 2018-12-22 03:00:00+00:00    5    3  53.277543

In [8]:
import numpy as np

resample_df = features

datetime_columns = ['Date', 'DOW', 'HOD']
target_column = 'ID3'

feature_columns = datetime_columns + ['ID3']

resample_df = resample_df[feature_columns]

## Plot ID3

In [9]:
import plotly.express as px

plot_length = 24*7 - 10
plot_df = resample_df.copy(deep=True).iloc[:plot_length]
# plot_df['weekday'] = plot_df['date'].dt.weekday_name
plot_df['DOW'] = plot_df['Date'].dt.day_name()

fig = px.line(plot_df,
              x="Date",
              y="ID3", 
              color="DOW", 
              title="Log of Appliance Energy Consumption vs Time")

fig.layout.font.family = 'SF Mono'

fig.show()

# Prepare Training Data

For this example, we will use sliding windows of 10 points per each window (equivalent to 10 hours) to predict each next point. The window size can be altered via the `sequence_length` variable.

Min-Max scaling has also been fitted to the training data to aid the convergence of the neural network. 

In [10]:
from sklearn.preprocessing import MinMaxScaler

def create_sliding_window(data, sequence_length, lag, stride=1):
    X_list, y_list = [], []
    for i in range(len(data)):
      if (i + sequence_length+lag) < len(data):
        X_list.append(data.iloc[i:i+sequence_length:stride, :].values)
        y_list.append(data.iloc[i+sequence_length+lag, -1])
    return np.array(X_list), np.array(y_list)

train_split = 0.7
n_train = int(train_split * len(resample_df))
n_test = len(resample_df) - n_train

# features = ['DOW', 'HOD', 'ID3']
features = ['ID3']
feature_array = resample_df[features].values

# Fit Scaler only on Training features
feature_scaler = MinMaxScaler()
feature_scaler.fit(feature_array[:n_train])
# Fit Scaler only on Training target values
target_scaler = MinMaxScaler()
target_scaler.fit(feature_array[:n_train, -1].reshape(-1, 1))

# Transfom on both Training and Test data
scaled_array = pd.DataFrame(feature_scaler.transform(feature_array),
                            columns=features)

# scaled_array = pd.DataFrame(feature_array)

sequence_length = 6
lag = 3
X, y = create_sliding_window(scaled_array, 
                             sequence_length, lag)

X_train = X[:n_train]
y_train = y[:n_train]

X_test = X[n_train:]
y_test = y[n_train:]

In [11]:
X_test.shape

(10145, 6, 1)

In [12]:
features[n_train:]

[]

In [13]:
# Convert the 3-D shape of X_train to a data frame so we can see: 
X_train_see = pd.DataFrame(np.reshape(X_train, (X_train.shape[0], X_train.shape[1])))
y_train_see = pd.DataFrame(y_train)
pd.concat([X_train_see, y_train_see], axis=1)

# Convert the 3-D shape of X_test to a data frame so we can see: 
X_test_see = pd.DataFrame(np.reshape(X_test, (X_test.shape[0], X_test.shape[1])))
y_test_see = pd.DataFrame(y_test)
pd.concat([X_test_see, y_test_see], axis=1)

print(), print(colored(f'There are {X_train.shape[0]} samples in the training data', 'green'))
print(colored(f'There are {X_test.shape[0]} samples in the test data', 'green')), print()

print(X_test_see.head(20))
print(y_test_see.head(20))


There are 23691 samples in the training data
There are 10145 samples in the test data

           0         1         2         3         4         5
0   0.116841  0.109414  0.097714  0.096207  0.091163  0.057219
1   0.109414  0.097714  0.096207  0.091163  0.057219  0.063441
2   0.097714  0.096207  0.091163  0.057219  0.063441  0.125564
3   0.096207  0.091163  0.057219  0.063441  0.125564  0.148602
4   0.091163  0.057219  0.063441  0.125564  0.148602  0.151270
5   0.057219  0.063441  0.125564  0.148602  0.151270  0.149450
6   0.063441  0.125564  0.148602  0.151270  0.149450  0.135165
7   0.125564  0.148602  0.151270  0.149450  0.135165  0.170054
8   0.148602  0.151270  0.149450  0.135165  0.170054  0.172706
9   0.151270  0.149450  0.135165  0.170054  0.172706  0.176532
10  0.149450  0.135165  0.170054  0.172706  0.176532  0.137132
11  0.135165  0.170054  0.172706  0.176532  0.137132  0.131465
12  0.170054  0.172706  0.176532  0.137132  0.131465  0.152141
13  0.172706  0.176532  0.1371

In [14]:
# features[features['ID3'] == 46.178149]

# features[n_train:].head(20)

# Define Bayesian LSTM Architecture

To demonstrate a simple working example of the Bayesian LSTM, the model as defined in Uber's paper has been used a starting point. The network architecture is as follows:

Encoder-Decoder Stage:
 - 1 uni-directional LSTM layer with 128 hidden units acts as an encoding layer to construct a fixed-dimension embedding state
 - 1 uni-directional LSTM layer with 32 hidden units acts as a decoding layer to produce predictions at future steps
 - Dropout is applied at **both** training and inference for both LSTM layers


 Predictor Stage:
 - 1 fully-connected output layer with 1 output (for predicting the target value) to produce a single value for the target variable


By allowing dropout at both training and testing time, the model simulates random sampling, thus allowing varying predictions that can be used to estimate the underlying distribution of the target value, enabling explicit model uncertainties.


In [15]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable

class BayesianLSTM(nn.Module):

    def __init__(self, n_features, output_length):

        super(BayesianLSTM, self).__init__()

        self.hidden_size_1 = 128
        self.hidden_size_2 = 32
        self.n_layers = 1 # number of (stacked) LSTM layers

        self.lstm1 = nn.LSTM(n_features, 
                             self.hidden_size_1, 
                             num_layers=1,
                             batch_first=True)
        self.lstm2 = nn.LSTM(self.hidden_size_1,
                             self.hidden_size_2,
                             num_layers=1,
                             batch_first=True)
        
        self.dense = nn.Linear(self.hidden_size_2, output_length)
        self.loss_fn = nn.MSELoss()
        
    def forward(self, x):
        batch_size, seq_len, _ = x.size()

        hidden = self.init_hidden1(batch_size)
        output, _ = self.lstm1(x, hidden)
        output = F.dropout(output, p=0.5, training=True)
        state = self.init_hidden2(batch_size)
        output, state = self.lstm2(output, state)
        output = F.dropout(output, p=0.5, training=True)
        output = self.dense(state[0].squeeze(0))
        
        return output
        
    def init_hidden1(self, batch_size):
        hidden_state = Variable(torch.zeros(self.n_layers, batch_size, self.hidden_size_1))
        cell_state = Variable(torch.zeros(self.n_layers, batch_size, self.hidden_size_1))
        return hidden_state, cell_state
    
    def init_hidden2(self, batch_size):
        hidden_state = Variable(torch.zeros(self.n_layers, batch_size, self.hidden_size_2))
        cell_state = Variable(torch.zeros(self.n_layers, batch_size, self.hidden_size_2))
        return hidden_state, cell_state
    
    def loss(self, pred, truth):
        return self.loss_fn(pred, truth)

    def predict(self, X):
        return self(torch.tensor(X, dtype=torch.float32)).view(-1).detach().numpy()

### Begin Training

To train the Bayesian LSTM, we use the ADAM optimizer along with mini-batch gradient descent (`batch_size = 128`). For quick demonstration purposes, the model is trained for 150 epochs.

The Bayesian LSTM is trained on the first 70% of data points, using the aforementioned sliding windows of size 10. The remaining 30% of the dataset is held out purely for testing.

In [16]:
n_features = scaled_array.shape[-1]
# n_features = inputs.shape[1]
# sequence_length = 10
output_length = 1

bayesian_lstm = BayesianLSTM(n_features=n_features,
                             output_length=output_length)

criterion = torch.nn.MSELoss()
optimizer = torch.optim.Adam(bayesian_lstm.parameters(), lr=0.001)

batch_size = 16
n_epochs = 12

In [17]:
bayesian_lstm.train()

for e in range(1, n_epochs+1):
    for b in range(0,len(X_train),batch_size):
        features = X_train[b:b+batch_size,:,:]
        target = y_train[b:b+batch_size]    

        X_batch = torch.tensor(features,dtype=torch.float32)    
        y_batch = torch.tensor(target,dtype=torch.float32)

        output = bayesian_lstm(X_batch) 
        loss = criterion(output.view(-1), y_batch)  

        loss.backward()
        optimizer.step()        
        optimizer.zero_grad() 

    if e % 1 == 0:
      print(f'epoch: {e}/{n_epochs}', 'loss: ', loss.item())

epoch: 1/12 loss:  0.003212454728782177
epoch: 2/12 loss:  0.0029132552444934845
epoch: 3/12 loss:  0.002763643627986312
epoch: 4/12 loss:  0.0025191488675773144
epoch: 5/12 loss:  0.0022466389928013086
epoch: 6/12 loss:  0.0020629027858376503
epoch: 7/12 loss:  0.002074230695143342
epoch: 8/12 loss:  0.0019117573974654078
epoch: 9/12 loss:  0.00188067730050534
epoch: 10/12 loss:  0.0018991467077285051
epoch: 11/12 loss:  0.0017621648730710149
epoch: 12/12 loss:  0.0017937413649633527


In [18]:
X_test.shape

bayesian_lstm.predict(X_test)

array([0.10231282, 0.10857067, 0.14713873, ..., 0.1514619 , 0.15844128,
       0.15783855], dtype=float32)

# Evaluating Model Performance

The Bayesian LSTM implemented is shown to produce reasonably accurate and sensible results on both the training and test sets, often comparable to other existing frequentist machine learning and deep learning methods.



In [19]:
offset = sequence_length + lag

def inverse_transform(y):
  return target_scaler.inverse_transform(y.reshape(-1, 1))

training_df = pd.DataFrame()
training_df['Date'] = resample_df['Date'].iloc[offset:n_train + offset:1] 
training_predictions = bayesian_lstm.predict(X_train)
training_df['ID3'] = inverse_transform(training_predictions)
training_df['Source'] = 'Training Prediction'

training_truth_df = pd.DataFrame()
training_truth_df['Date'] = training_df['Date']
training_truth_df['ID3'] = resample_df['ID3'].iloc[offset:n_train + offset:1] 
training_truth_df['Source'] = 'True Values'

testing_df = pd.DataFrame()
testing_df['Date'] = resample_df['Date'].iloc[n_train + offset::1] 
testing_predictions = bayesian_lstm.predict(X_test)
testing_df['ID3'] = inverse_transform(testing_predictions)
testing_df['Source'] = 'Test Prediction'

testing_truth_df = pd.DataFrame()
testing_truth_df['Date'] = testing_df['Date']
testing_truth_df['ID3'] = resample_df['ID3'].iloc[n_train + offset::1] 
testing_truth_df['Source'] = 'True Values'

evaluation = pd.concat([training_df, 
                        testing_df,
                        training_truth_df,
                        testing_truth_df
                        ], axis=0)

In [20]:
testing_df['Date']

23700   2017-10-22 06:00:00+00:00
23701   2017-10-22 07:00:00+00:00
23702   2017-10-22 08:00:00+00:00
23703   2017-10-22 09:00:00+00:00
23704   2017-10-22 10:00:00+00:00
                   ...           
33840   2018-12-21 23:00:00+00:00
33841   2018-12-22 00:00:00+00:00
33842   2018-12-22 01:00:00+00:00
33843   2018-12-22 02:00:00+00:00
33844   2018-12-22 03:00:00+00:00
Name: Date, Length: 10145, dtype: datetime64[ns, UTC]

In [21]:
fig = px.line(evaluation.loc[evaluation['Date'].between('2015-01-01', '2018-12-01')],
                 x="Date",
                 y="ID3",
                 color="Source",
                 title="Log of Appliance Energy Consumption in Wh vs Time")
fig.show()

# Uncertainty Quantification

The fact that stochastic dropouts are applied after each LSTM layer in the Bayesian LSTM enables users to interpret the model outputs as random samples from the posterior distribution of the target variable. 

This implies that by running multiple experiments/predictions, can approximate  parameters of the posterioir distribution, namely the mean and the variance, in order to create confidence intervals for each prediction.

In this example, we construct 99% confidence intervals that are three standard deviations away from the approximate mean of each prediction.

In [22]:
n_experiments = 100

test_uncertainty_df = pd.DataFrame()
test_uncertainty_df['Date'] = testing_df['Date']

for i in range(1, n_experiments + 1):
  experiment_predictions = bayesian_lstm.predict(X_test)
  test_uncertainty_df['ID3_{}'.format(i)] = inverse_transform(experiment_predictions)
  
  if i % 1 == 0:
    print(f'Experiment: {i}/{n_experiments}')

log_energy_consumption_df = test_uncertainty_df.filter(like='ID3', axis=1)
test_uncertainty_df['ID3_mean'] = log_energy_consumption_df.mean(axis=1)
test_uncertainty_df['ID3_std'] = log_energy_consumption_df.std(axis=1)

test_uncertainty_df = test_uncertainty_df[['Date', 'ID3_mean', 'ID3_std']]

Experiment: 1/100
Experiment: 2/100
Experiment: 3/100
Experiment: 4/100
Experiment: 5/100
Experiment: 6/100
Experiment: 7/100
Experiment: 8/100
Experiment: 9/100
Experiment: 10/100
Experiment: 11/100
Experiment: 12/100
Experiment: 13/100
Experiment: 14/100
Experiment: 15/100
Experiment: 16/100
Experiment: 17/100
Experiment: 18/100
Experiment: 19/100
Experiment: 20/100
Experiment: 21/100
Experiment: 22/100
Experiment: 23/100
Experiment: 24/100
Experiment: 25/100
Experiment: 26/100
Experiment: 27/100
Experiment: 28/100
Experiment: 29/100
Experiment: 30/100
Experiment: 31/100
Experiment: 32/100
Experiment: 33/100
Experiment: 34/100
Experiment: 35/100
Experiment: 36/100
Experiment: 37/100
Experiment: 38/100
Experiment: 39/100
Experiment: 40/100
Experiment: 41/100
Experiment: 42/100
Experiment: 43/100
Experiment: 44/100
Experiment: 45/100
Experiment: 46/100
Experiment: 47/100
Experiment: 48/100
Experiment: 49/100
Experiment: 50/100
Experiment: 51/100
Experiment: 52/100
Experiment: 53/100
Ex

In [23]:
test_uncertainty_df['lower_bound'] = test_uncertainty_df['ID3_mean'] - 3*test_uncertainty_df['ID3_std']
test_uncertainty_df['upper_bound'] = test_uncertainty_df['ID3_mean'] + 3*test_uncertainty_df['ID3_std']

test_uncertainty_df.head(20)

Date   ID3_mean   ID3_std  lower_bound  upper_bound
23700 2017-10-22 06:00:00+00:00  30.664959  1.550294    26.014078    35.315842
23701 2017-10-22 07:00:00+00:00  31.824236  1.548112    27.179901    36.468571
23702 2017-10-22 08:00:00+00:00  46.046024  1.427787    41.762665    50.329384
23703 2017-10-22 09:00:00+00:00  50.178349  1.293144    46.298916    54.057781
23704 2017-10-22 10:00:00+00:00  45.823685  1.387422    41.661419    49.985950
23705 2017-10-22 11:00:00+00:00  41.865284  1.302567    37.957581    45.772987
23706 2017-10-22 12:00:00+00:00  40.034203  1.171314    36.520260    43.548145
23707 2017-10-22 13:00:00+00:00  49.780357  1.454664    45.416367    54.144348
23708 2017-10-22 14:00:00+00:00  51.385132  1.401862    47.179546    55.590717
23709 2017-10-22 15:00:00+00:00  50.420914  1.017592    47.368137    53.473690
23710 2017-10-22 16:00:00+00:00  41.061390  1.270987    37.248428    44.874352
23711 2017-10-22 17:00:00+00:00  40.535496  1.115860    37.187916    43.883076
23712 2017-10-22 18:00:00+00:00  48.023540  1.220600    44.361740    51.685341
23713 2017-10-22 19:00:00+00:00  50.813114  1.223765    47.141819    54.484409
23714 2017-10-22 20:00:00+00:00  53.915855  1.226123    50.237488    57.594223
23715 2017-10-22 21:00:00+00:00  49.685810  0.990579    46.714073    52.657547
23716 2017-10-22 22:00:00+00:00  48.505234  1.150731    45.053040    51.957428
23717 2017-10-22 23:00:00+00:00  49.223698  1.071527    46.009117    52.438278
23718 2017-10-23 00:00:00+00:00  46.998486  0.923018    44.229431    49.767540
23719 2017-10-23 01:00:00+00:00  38.360790  1.240396    34.639603    42.081978

In [24]:
import plotly.graph_objects as go

# datespan = '2018-10-01', '2018-10-04'

test_uncertainty_plot_df = test_uncertainty_df.copy(deep=True)
test_uncertainty_plot_df = test_uncertainty_plot_df.loc[test_uncertainty_plot_df['Date'].between('2016-08-01', '2018-10-04')]
truth_uncertainty_plot_df = testing_truth_df.copy(deep=True)
truth_uncertainty_plot_df = truth_uncertainty_plot_df.loc[testing_truth_df['Date'].between('2016-08-01', '2018-10-04')]

upper_trace = go.Scatter(
    x=test_uncertainty_plot_df['Date'],
    y=test_uncertainty_plot_df['upper_bound'],
    mode='lines',
    fill=None,
    name='99% Upper Confidence Bound'
    )
lower_trace = go.Scatter(
    x=test_uncertainty_plot_df['Date'],
    y=test_uncertainty_plot_df['lower_bound'],
    mode='lines',
    fill='tonexty',
    fillcolor='rgba(255, 211, 0, 0.5)',
    name='99% Lower Confidence Bound'
    )
real_trace = go.Scatter(
    x=truth_uncertainty_plot_df['Date'],
    y=truth_uncertainty_plot_df['ID3'],
    mode='lines',
    fill=None,
    name='Real Values'
    )
mean_trace = go.Scatter(
    x=truth_uncertainty_plot_df['Date'],
    y=test_uncertainty_plot_df['ID3_mean'],
    mode='lines',
    fill=None,
    name='Mean Values'
    )

data = [upper_trace, lower_trace, real_trace, mean_trace]

fig = go.Figure(data=data)
fig.update_layout(title='Uncertainty Quantification for Energy Consumption Test Data',
                   xaxis_title='Time',
                   yaxis_title='log_energy_consumption (log Wh)')

fig.layout.font.family = 'SF Mono'

fig.show()

#### Evaluating Uncertainty

Using multiple experiments above, 99% confidence intervals have been constructed for each the prediction of the target variable (the logarithm of appliance power consumption). While we can visually observe that the model is generally capturing the behavior of the time-series, approximately only 50% of the real data points lie within a 99% confidence interval from the mean prediction value.

Despite the relatively low percentage of points within the confidence interval, it must be noted that Bayesian Neural Networks only seek to quantify the epistemic model uncertainty and does not account for aleatoric uncertainty (i.e. noise).

In [25]:
bounds_df = pd.DataFrame()

# Using 99% confidence bounds
bounds_df['lower_bound'] = test_uncertainty_plot_df['lower_bound']
bounds_df['prediction'] = test_uncertainty_plot_df['ID3_mean']
bounds_df['real_value'] = truth_uncertainty_plot_df['ID3']
bounds_df['upper_bound'] = test_uncertainty_plot_df['upper_bound']

bounds_df['contained'] = ((bounds_df['real_value'] >= bounds_df['lower_bound']) &
                          (bounds_df['real_value'] <= bounds_df['upper_bound']))

print("Proportion of points contained within 99% confidence interval:", 
      bounds_df['contained'].mean())

Proportion of points contained within 99% confidence interval: 0.22895949551297598


# Conclusions

- Bayesian LSTMs have been able to produce comparable performance to their frequentist counterparts (all else being equal)
- Stochastic dropout enables users to approximate the posterior distribution of the target variable, \
and thus construct confidence intervals for each prediction 
- Bayesian Neural Networks only attempt to account for epistemic model uncertainty and do not necessarily address aleatoric uncertainty
- Computational overhead for repeated/multiple Bayesian LSTM predictions at inference to construct confidence intervals represent a potential challenge for real-time inference use-cases.